In [ ]:
import numpy as np
import time, csv
import matplotlib.pyplot as plt
from pathlib import Path

# MPC 관련 모듈
from APMonitor.apm import apm_web        
from mpc_lib import mpc_init, mpc          

# 시뮬레이터 or 실제 키트 선택
simulated = True
if simulated:
    from tclab import setup
    lab = setup(connected=False)
    arduino = lab(synced=False)
else:
    import tclab
    arduino = tclab.TCLab()

class MPCDataCollector:

    def __init__(
        self,
        episodes: int = 5,
        total_time_sec: int = 1200,
        sample_interval: float = 5.0,
        start_temp: float = 29.0,
        setpoint_range: tuple = (25.0, 65.0),
        data_dir: Path = Path('./eval_data_simulator')
    ):
        self.total_time = total_time_sec
        self.dt = sample_interval
        self.steps = int(total_time_sec / sample_interval)

        self.episodes = episodes
        self.start_temp = start_temp
        self.sp_low, self.sp_high = setpoint_range

        self.csv_dir = data_dir / 'csv'
        self.png_dir = data_dir / 'png'
        self.csv_dir.mkdir(parents=True, exist_ok=True)
        self.png_dir.mkdir(parents=True, exist_ok=True)
    def generate_random_tsp(self) -> np.ndarray:
            """
            Set-point 구간별 정보를 로그로 출력.
            각 구간 길이: 평균 480초, σ 100초, 최소 160초, 최대 800초
            """
            tsp = np.zeros(self.steps)
            i = 0
            seg_id = 1  # 구간 번호
            print(f"\n--- Set-point 프로파일 생성 (총 시간: {self.total_time}초, 총 step: {self.steps}) ---")
            while i < self.steps:
                dur_sec = int(np.clip(np.random.normal(480, 100), 160, 800))
                dur_steps = max(1, int(dur_sec / self.dt))
                end = min(i + dur_steps, self.steps)
        
                # set-point 값 설정
                temp = round(np.random.uniform(self.sp_low, self.sp_high), 2)
                tsp[i:end] = temp
        
                # 로그 출력
                start_time = int(i * self.dt)
                end_time = int((end - 1) * self.dt)
                print(f"구간 {seg_id}: step {i:>3} ~ {end-1:>3} (시간 {start_time:>4}s ~ {end_time:>4}s) → 목표 온도: {temp:.2f}°C")
        
                i = end
                seg_id += 1
            print("-----------------------------------------------------------\n")
            return tsp

    def save_plot(self, t, T1, Tsp1, T2, Tsp2, Q1, Q2, ep):
        fig, axs = plt.subplots(2, 1, figsize=(10, 8))
        axs[0].plot(t, T1,  'b-', label='T1 (measured)')
        axs[0].plot(t, Tsp1,'k--',label='T1 (setpoint)')
        axs[0].plot(t, T2,  'r-', label='T2 (measured)')
        axs[0].plot(t, Tsp2,'k:', label='T2 (setpoint)')
        axs[0].set_ylabel('Temperature (°C)')
        axs[0].legend(); axs[0].grid()

        axs[1].plot(t, Q1, 'b-', label='Q1')
        axs[1].plot(t, Q2, 'r--', label='Q2')
        axs[1].set_ylabel('Heater Output (%)')
        axs[1].set_xlabel('Time (s)')
        axs[1].legend(); axs[1].grid()

        plt.tight_layout()
        plt.savefig(self.png_dir / f'mpc_episode_{ep}.png')
        plt.close()

    def run_episode(self, arduino, ep: int, epi_seed: int):
        print(f"\n=== Episode {ep} (seed={epi_seed}) start ===")
        np.random.seed(epi_seed)

        arduino.Q1(0); arduino.Q2(0)
        if simulated:
            # ✅ 시뮬레이터일 경우: 직접 설정
            arduino.Q1(0); arduino.Q2(0)
            arduino._T1 = arduino._T2 = self.start_temp - 1.0  # 바로 28도로 초기화
            arduino.update(t=0)
            print(f"✅ 시뮬레이터 초기 온도 설정: T1={arduino.T1:.1f}, T2={arduino.T2:.1f}")
        else:
            arduino.Q1(0); arduino.Q2(0)
            while arduino.T1 >= self.start_temp or arduino.T2 >= self.start_temp:
                print(f" Cooling... T1={arduino.T1:.1f}, T2={arduino.T2:.1f}")
                time.sleep(20)

        t = np.zeros(self.steps)
        T1 = np.zeros(self.steps); T2 = np.zeros(self.steps)
        Q1 = np.zeros(self.steps); Q2 = np.zeros(self.steps)
        Tsp1 = self.generate_random_tsp()
        Tsp2 = self.generate_random_tsp()
        iae = 0.0

        csv_path = self.csv_dir / f'mpc_episode_{ep}_data.csv'
        with open(csv_path, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['Episode','Time','T1','T2','Q1','Q2','TSP1','TSP2','IAE'])

            mpc_init()
            for k in range(self.steps):
                loop_start = time.time()
                t[k] = k * self.dt

                arduino.update(t=t[k]) if simulated else None

                T1[k] = round(arduino.T1, 2)
                T2[k] = round(arduino.T2, 2)
                iae += abs(Tsp1[k] - T1[k]) + abs(Tsp2[k] - T2[k])

                q1, q2 = mpc(T1[k], Tsp1[k], T2[k], Tsp2[k])
                Q1[k] = round(q1, 2); Q2[k] = round(q2, 2)
                arduino.Q1(Q1[k]); arduino.Q2(Q2[k])

                if k % 12 == 0 or k == self.steps - 1:
                    print(f" t={t[k]:4.0f}s | "
                          f"SP1={Tsp1[k]:5.2f}, PV1={T1[k]:5.2f}, Q1={Q1[k]:5.2f} | "
                          f"SP2={Tsp2[k]:5.2f}, PV2={T2[k]:5.2f}, Q2={Q2[k]:5.2f} | "
                          f"IAE={iae:7.2f}")

                writer.writerow([
                    ep, f"{t[k]:.0f}",
                    f"{T1[k]:.2f}", f"{T2[k]:.2f}",
                    f"{Q1[k]:.2f}", f"{Q2[k]:.2f}",
                    f"{Tsp1[k]:.2f}", f"{Tsp2[k]:.2f}",
                    f"{iae:.2f}"
                ])

                elapsed = time.time() - loop_start
                time.sleep(max(0.0, self.dt - elapsed))

        self.save_plot(t, T1, Tsp1, T2, Tsp2, Q1, Q2, ep)
        print(f"=== Episode {ep} done, data saved to {csv_path} ===")

    def run(self):
        epi_seeds = [3,4]
        arduino.LED(100)
        for ep, seed in enumerate(epi_seeds, start=1):
            self.run_episode(arduino, ep, seed)
        arduino.close()
        print("All episodes finished.")

# 실행
collector = MPCDataCollector()
collector.run()


TCLab version 1.0.0
Simulated TCLab

=== Episode 1 (seed=1) start ===
✅ 시뮬레이터 초기 온도 설정: T1=27.7, T2=28.0

--- Set-point 프로파일 생성 (총 시간: 1200초, 총 step: 240) ---
구간 1: step   0 ~ 127 (시간    0s ~  635s) → 목표 온도: 25.00°C
구간 2: step 128 ~ 210 (시간  640s ~ 1050s) → 목표 온도: 37.09°C
구간 3: step 211 ~ 239 (시간 1055s ~ 1195s) → 목표 온도: 40.87°C
-----------------------------------------------------------


--- Set-point 프로파일 생성 (총 시간: 1200초, 총 step: 240) ---
구간 1: step   0 ~  73 (시간    0s ~  365s) → 목표 온도: 46.55°C
구간 2: step  74 ~ 203 (시간  370s ~ 1015s) → 목표 온도: 33.18°C
구간 3: step 204 ~ 239 (시간 1020s ~ 1195s) → 목표 온도: 60.12°C
-----------------------------------------------------------

apm 220.76.61.147_my_mpc <br><pre> ----------------------------------------------------------------
 APMonitor, Version 1.0.3
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :            0
  

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
from scipy.interpolate import interp1d

def compute_reward(t1, t2, tsp1, tsp2):
    return -np.sqrt((t1 - tsp1)**2 + (t2 - tsp2)**2)

def compute_errors(t1, t2, tsp1, tsp2):
    e1 = np.abs(t1 - tsp1)
    e2 = np.abs(t2 - tsp2)
    over = np.where(t1 > tsp1, t1 - tsp1, 0) + np.where(t2 > tsp2, t2 - tsp2, 0)
    under = np.where(t1 < tsp1, tsp1 - t1, 0) + np.where(t2 < tsp2, tsp2 - t2, 0)
    return e1.sum(), e2.sum(), over.sum(), under.sum()

def interpolate_df(df, original_dt=5.0, target_dt=1.0):
    n_points = len(df)
    original_t = np.arange(n_points) * original_dt
    new_t = np.arange(0, original_t[-1] + target_dt, target_dt)

    interp_cols = ['T1', 'T2', 'TSP1', 'TSP2', 'Q1', 'Q2']
    interpolated = {}
    for col in interp_cols:
        f = interp1d(original_t, df[col], kind='linear', fill_value='extrapolate')
        interpolated[col] = f(new_t)

    interpolated['time'] = new_t
    return pd.DataFrame(interpolated)

def process_mpc_folder(csv_folder: Path, save_folder: Path):
    csv_files = sorted(csv_folder.glob("mpc_episode_*_data.csv"))
    results = []

    for csv_path in csv_files:
        df = pd.read_csv(csv_path)
        df_interp = interpolate_df(df)

        t1 = df_interp['T1'].values
        t2 = df_interp['T2'].values
        tsp1 = df_interp['TSP1'].values
        tsp2 = df_interp['TSP2'].values

        # 계산
        rewards = compute_reward(t1, t2, tsp1, tsp2)
        total_return = rewards.sum()

        e1, e2, over, under = compute_errors(t1, t2, tsp1, tsp2)
        total_error = e1 + e2  # 또는 + over + under

        # 그래프 저장
        fig, ax = plt.subplots(2, 1, figsize=(10, 6))
        t = df_interp['time']
        ax[0].plot(t, t1, label='T1')
        ax[0].plot(t, tsp1, '--', label='TSP1')
        ax[0].plot(t, t2, label='T2')
        ax[0].plot(t, tsp2, '--', label='TSP2')
        ax[0].legend(); ax[0].set_ylabel('Temperature'); ax[0].grid()

        ax[1].plot(t, df_interp['Q1'], label='Q1')
        ax[1].plot(t, df_interp['Q2'], label='Q2')
        ax[1].legend(); ax[1].set_ylabel('Heater (%)'); ax[1].set_xlabel('Time (s)'); ax[1].grid()

        plt.tight_layout()
        fig_name = save_folder / f"{csv_path.stem}_interp.png"
        plt.savefig(fig_name)
        plt.close()

        results.append({
            'file': csv_path.name,
            'return': total_return,
            'E1': e1,
            'E2': e2,
            'Over': over,
            'Under': under,
            'total_error': total_error
        })

    return pd.DataFrame(results)

# 🟢 실행
csv_folder = Path("C:\\Users\\Developer\\TCLab\\IQL\\src\\eval_data_simulator\\csv")   # 수정 가능
save_folder = Path("C:/Users/Developer/TCLab/interp_plot")
save_folder.mkdir(exist_ok=True)

result_df = process_mpc_folder(csv_folder, save_folder)
from IPython.display import display
display(result_df[['file', 'return', 'total_error']])


file        return  total_error
0  mpc_episode_1_data.csv -10511.154964    13160.210
1  mpc_episode_2_data.csv -10611.301910    11881.934
2  mpc_episode_3_data.csv  -6806.361915     8822.626
3  mpc_episode_4_data.csv  -6005.054868     7167.290
4  mpc_episode_5_data.csv -12146.785771    13271.680